In [28]:
import pandas as pd
import numpy as np
from numpy import *

import statsmodels.api as sm
import statsmodels.formula.api as smf
from statsmodels.tools.tools import add_constant

from sklearn.decomposition import PCA
from sklearn.linear_model import LinearRegression, Ridge

import tensorflow as tf
from tensorflow import keras
# 这里就是jupyter的运行时清屏函数，虽然不知道什么原理，回头再来学
import sys
import os
def clear_output():
    """
    clear output for both jupyter notebook and the console
    """
    os.system('cls' if os.name == 'nt' else 'clear')
    if 'ipykernel' in sys.modules:
        from IPython.display import clear_output as clear
        clear()


import copy
import itertools
import random
import warnings
warnings.filterwarnings('ignore')
import time
from sklearn.metrics import mean_squared_error, make_scorer

# DATA

In [29]:
# 样本外区间
oos_start_date = '2000-01'
oos_end_date = '2020-12'
holdout_period = 6*12 

In [30]:
#读取原始数据
data0 = pd.read_csv("@data/data_1981-01_2020-12_value.csv")
factors = pd.read_csv("@data/fac_cols.csv")['0'].tolist()
bond = pd.read_csv("@data/bond_cols.csv")['0'].tolist()
lag_bond = pd.read_csv("@data/lag_bond_cols.csv")['0'].tolist()
#data copy
data = data0.copy()
#OOS区间
oos_start_idx = data[data['month'].astype(str) == oos_start_date].index[0]
oos_end_idx = data[data['month'].astype(str) == oos_end_date].index[0]
holdout_start_idx = oos_start_idx - holdout_period
#计算y mean
for bond_group in bond:
    for t in range(len(data)):
        data.loc[t,'mean_' + bond_group] = mean(data.loc[:t,'lag_' + bond_group])

In [31]:
def r2_oos_mean(y_true, y_pred, y_mean_pred): #普通R方
    return 1 - np.sum((y_true - y_pred)**2) / np.sum((y_true-y_mean_pred)**2)

In [32]:
len(factors)

22

In [33]:
data["ALL"]

0     -0.003091
1     -0.013946
2      0.009574
3     -0.033375
4      0.009176
         ...   
475    0.002278
476   -0.001622
477    0.001310
478    0.005592
479    0.002901
Name: ALL, Length: 480, dtype: float64

# Transformer

In [34]:
import numpy as np
import pandas as pd
import os, datetime
import tensorflow as tf
from tensorflow.keras.models import *
from tensorflow.keras.layers import *
print('Tensorflow version: {}'.format(tf.__version__))

import matplotlib.pyplot as plt
plt.style.use('seaborn')

import warnings
warnings.filterwarnings('ignore')

Tensorflow version: 2.0.0


In [35]:
batch_size = 32
seq_len = 12

d_k = 256
d_v = 256
n_heads = 12
ff_dim = 256

In [36]:
class Time2Vector(Layer):
    def __init__(self, seq_len, **kwargs):
        super(Time2Vector, self).__init__()
        self.seq_len = seq_len

    def build(self, input_shape):
        '''Initialize weights and biases with shape (batch, seq_len)'''
        self.weights_linear = self.add_weight(name='weight_linear',
                                    shape=(int(self.seq_len),),
                                    initializer='uniform',
                                    trainable=True)

        self.bias_linear = self.add_weight(name='bias_linear',
                                    shape=(int(self.seq_len),),
                                    initializer='uniform',
                                    trainable=True)

        self.weights_periodic = self.add_weight(name='weight_periodic',
                                    shape=(int(self.seq_len),),
                                    initializer='uniform',
                                    trainable=True)

        self.bias_periodic = self.add_weight(name='bias_periodic',
                                    shape=(int(self.seq_len),),
                                    initializer='uniform',
                                    trainable=True)
    def call(self, x):
        '''Calculate linear and periodic time features'''
        x = tf.math.reduce_mean(x[:,:,:21], axis=-1)
        time_linear = self.weights_linear * x + self.bias_linear # Linear time feature
        time_linear = tf.expand_dims(time_linear, axis=-1) # Add dimension (batch, seq_len, 1)

        time_periodic = tf.math.sin(tf.multiply(x, self.weights_periodic) + self.bias_periodic)
        time_periodic = tf.expand_dims(time_periodic, axis=-1) # Add dimension (batch, seq_len, 1)
        return tf.concat([time_linear, time_periodic], axis=-1) # shape = (batch, seq_len, 2)
    def get_config(self): # Needed for saving and loading model with custom layer
        config = super().get_config().copy()
        config.update({'seq_len': self.seq_len})
        return config

In [37]:
class SingleAttention(Layer):
    def __init__(self, d_k, d_v):
        super(SingleAttention, self).__init__()
        self.d_k = d_k
        self.d_v = d_v

    def build(self, input_shape):
        self.query = Dense(self.d_k, 
                           input_shape=input_shape, 
                           kernel_initializer='glorot_uniform', 
                           bias_initializer='glorot_uniform')

        self.key = Dense(self.d_k, 
                         input_shape=input_shape, 
                         kernel_initializer='glorot_uniform', 
                         bias_initializer='glorot_uniform')

        self.value = Dense(self.d_v, 
                           input_shape=input_shape, 
                           kernel_initializer='glorot_uniform', 
                           bias_initializer='glorot_uniform')

    def call(self, inputs): # inputs = (in_seq, in_seq, in_seq)
        q = self.query(inputs[0])
        k = self.key(inputs[1])

        attn_weights = tf.matmul(q, k, transpose_b=True)
        attn_weights = tf.map_fn(lambda x: x/np.sqrt(self.d_k), attn_weights)
        attn_weights = tf.nn.softmax(attn_weights, axis=-1)

        v = self.value(inputs[2])
        attn_out = tf.matmul(attn_weights, v)
        return attn_out    

#############################################################################

class MultiAttention(Layer):
    def __init__(self, d_k, d_v, n_heads):
        super(MultiAttention, self).__init__()
        self.d_k = d_k
        self.d_v = d_v
        self.n_heads = n_heads
        self.attn_heads = list()

    def build(self, input_shape):
        for n in range(self.n_heads):
            self.attn_heads.append(SingleAttention(self.d_k, self.d_v))  

        # input_shape[0]=(batch, seq_len, 7), input_shape[0][-1]=7 
        self.linear = Dense(input_shape[0][-1], 
                            input_shape=input_shape, 
                            kernel_initializer='glorot_uniform', 
                            bias_initializer='glorot_uniform')

    def call(self, inputs):
        attn = [self.attn_heads[i](inputs) for i in range(self.n_heads)]
        concat_attn = tf.concat(attn, axis=-1)
        multi_linear = self.linear(concat_attn)
        return multi_linear   

#############################################################################

class TransformerEncoder(Layer):
    def __init__(self, d_k, d_v, n_heads, ff_dim, dropout=0.1, **kwargs):
        super(TransformerEncoder, self).__init__()
        self.d_k = d_k
        self.d_v = d_v
        self.n_heads = n_heads
        self.ff_dim = ff_dim
        self.attn_heads = list()
        self.dropout_rate = dropout

    def build(self, input_shape):
        self.attn_multi = MultiAttention(self.d_k, self.d_v, self.n_heads)
        self.attn_dropout = Dropout(self.dropout_rate)
        self.attn_normalize = LayerNormalization(input_shape=input_shape, epsilon=1e-6)

        self.ff_conv1D_1 = Conv1D(filters=self.ff_dim, kernel_size=1, activation='relu')
        # input_shape[0]=(batch, seq_len, 7), input_shape[0][-1] = 7 
        self.ff_conv1D_2 = Conv1D(filters=input_shape[0][-1], kernel_size=1) 
        self.ff_dropout = Dropout(self.dropout_rate)
        self.ff_normalize = LayerNormalization(input_shape=input_shape, epsilon=1e-6)    

    def call(self, inputs): # inputs = (in_seq, in_seq, in_seq)
        attn_layer = self.attn_multi(inputs)
        attn_layer = self.attn_dropout(attn_layer)
        attn_layer = self.attn_normalize(inputs[0] + attn_layer)

        ff_layer = self.ff_conv1D_1(attn_layer)
        ff_layer = self.ff_conv1D_2(ff_layer)
        ff_layer = self.ff_dropout(ff_layer)
        ff_layer = self.ff_normalize(inputs[0] + ff_layer)
        return ff_layer 

    def get_config(self): # Needed for saving and loading model with custom layer
        config = super().get_config().copy()
        config.update({'d_k': self.d_k,
                       'd_v': self.d_v,
                       'n_heads': self.n_heads,
                       'ff_dim': self.ff_dim,
                       'attn_heads': self.attn_heads,
                       'dropout_rate': self.dropout_rate})
        return config    

In [61]:
Time2Vector(seq_len)

In [38]:
time_embedding = Time2Vector(seq_len)

In [39]:
in_seq = Input(shape=(seq_len, 22))

In [40]:
time_embedding(in_seq)

<tf.Tensor 'time2_vector_2/Identity:0' shape=(None, 12, 2) dtype=float32>

In [41]:
def create_model():
    '''Initialize time and transformer layers'''
    time_embedding = Time2Vector(seq_len)
    attn_layer1 = TransformerEncoder(d_k, d_v, n_heads, ff_dim)
    attn_layer2 = TransformerEncoder(d_k, d_v, n_heads, ff_dim)
    attn_layer3 = TransformerEncoder(d_k, d_v, n_heads, ff_dim)

    '''Construct model'''
    in_seq = Input(shape=(seq_len, 22))
    x = time_embedding(in_seq)
    x = Concatenate(axis=-1)([in_seq, x])
    x = attn_layer1((x, x, x))
    x = attn_layer2((x, x, x))
    x = attn_layer3((x, x, x))
    x = GlobalAveragePooling1D(data_format='channels_first')(x)
    x = Dropout(0.1)(x)
    x = Dense(64, activation='relu')(x)
    x = Dropout(0.1)(x)
    out = Dense(1, activation='linear')(x)

    model = Model(inputs=in_seq, outputs=out)
    model.compile(loss='mse', optimizer='adam', metrics=['mae', 'mape'])
    return model

In [42]:
model = create_model()
model.summary()

Model: "model_1"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_4 (InputLayer)            [(None, 12, 22)]     0                                            
__________________________________________________________________________________________________
time2_vector_3 (Time2Vector)    (None, 12, 2)        48          input_4[0][0]                    
__________________________________________________________________________________________________
concatenate_1 (Concatenate)     (None, 12, 24)       0           input_4[0][0]                    
                                                                 time2_vector_3[0][0]             
__________________________________________________________________________________________________
transformer_encoder_3 (Transfor (None, 12, 24)       316816      concatenate_1[0][0]        

In [43]:
callback = tf.keras.callbacks.ModelCheckpoint('Transformer+TimeEmbedding.hdf5', 
                                              monitor='val_loss', 
                                              save_best_only=True, verbose=1)

# seq_len=1

In [29]:
valid = 5*12

In [30]:
def transformer_single_bond_oos(bond_group):
    tf.random.set_seed(33)
    y_preds = []
    for t in range(holdout_start_idx,oos_end_idx+1):
        x_train = data[factors][:t-valid]
        x_train = np.array(x_train)
        x_train = np.reshape(x_train, (-1, 1, 22))
#         print(x_train)
        y_train = data[bond_group][:t-valid]
        x_valid = data[factors][t-valid:t]
        x_valid = np.array(x_valid)
        x_valid = np.reshape(x_valid, (-1, 1, 22))
    #     print(x_valid)
        y_valid = data[bond_group][t-valid:t]
        x_pred = data[factors][t:t+1]
        x_pred = np.array(x_pred)
        x_pred = np.reshape(x_pred, (-1, 1, 22))
        y_train,y_valid = np.array(y_train), np.array(y_valid)
    #     print(x_test)
        trn = model.fit(x_train, y_train, 
                    batch_size=batch_size, 
                    epochs=20, 
                    callbacks=[callback],
                    validation_data=(x_valid, y_valid))  
    #     print(x_test)
    #     print(model.predict(x_test).tolist()[0][0])
        y_preds.append(model.predict(x_pred).tolist()[0][0])
#         clear_output()
    return y_preds

In [31]:
transformer_pred = pd.Series(transformer_single_bond_oos('ALL'))

Train on 96 samples, validate on 60 samples
Epoch 1/20
64/96 [===================>..........] - ETA: 36s - loss: 2.2020e-04 - mae: 0.0112 - mape: 145.7556 
Epoch 00001: val_loss improved from inf to 0.00012, saving model to Transformer+TimeEmbedding.hdf5
96/96 [==============================] - 78s 810ms/sample - loss: 2.2880e-04 - mae: 0.0116 - mape: 129.5849 - val_loss: 1.1882e-04 - val_mae: 0.0090 - val_mape: 104.7700
Epoch 2/20
64/96 [===================>..........] - ETA: 0s - loss: 2.0803e-04 - mae: 0.0108 - mape: 123.4458
Epoch 00002: val_loss did not improve from 0.00012
96/96 [==============================] - 0s 3ms/sample - loss: 2.2772e-04 - mae: 0.0117 - mape: 130.6114 - val_loss: 1.1927e-04 - val_mae: 0.0090 - val_mape: 102.1915
Epoch 3/20
64/96 [===================>..........] - ETA: 0s - loss: 2.0912e-04 - mae: 0.0107 - mape: 102.7973
Epoch 00003: val_loss did not improve from 0.00012
96/96 [==============================] - 0s 3ms/sample - loss: 2.2660e-04 - mae: 0.011

Epoch 5/20
96/97 [============================>.] - ETA: 0s - loss: 2.6124e-04 - mae: 0.0126 - mape: 150.3040
Epoch 00005: val_loss did not improve from 0.00012
97/97 [==============================] - 0s 3ms/sample - loss: 2.6016e-04 - mae: 0.0126 - mape: 150.1601 - val_loss: 1.5629e-04 - val_mae: 0.0106 - val_mape: 139.4283
Epoch 6/20
96/97 [============================>.] - ETA: 0s - loss: 2.3549e-04 - mae: 0.0120 - mape: 124.7806
Epoch 00006: val_loss did not improve from 0.00012
97/97 [==============================] - 0s 3ms/sample - loss: 2.3956e-04 - mae: 0.0121 - mape: 124.5208 - val_loss: 1.2365e-04 - val_mae: 0.0092 - val_mape: 95.6044
Epoch 7/20
96/97 [============================>.] - ETA: 0s - loss: 2.2414e-04 - mae: 0.0114 - mape: 123.8829
Epoch 00007: val_loss did not improve from 0.00012
97/97 [==============================] - 0s 3ms/sample - loss: 2.2215e-04 - mae: 0.0113 - mape: 123.1225 - val_loss: 1.2577e-04 - val_mae: 0.0091 - val_mape: 163.3137
Epoch 8/20
96/97 

Epoch 10/20
96/98 [============================>.] - ETA: 0s - loss: 2.1800e-04 - mae: 0.0113 - mape: 140.9341
Epoch 00010: val_loss did not improve from 0.00012
98/98 [==============================] - 0s 3ms/sample - loss: 2.1740e-04 - mae: 0.0113 - mape: 140.5168 - val_loss: 1.3242e-04 - val_mae: 0.0095 - val_mape: 98.1993
Epoch 11/20
96/98 [============================>.] - ETA: 0s - loss: 2.2610e-04 - mae: 0.0116 - mape: 100.4540
Epoch 00011: val_loss did not improve from 0.00012
98/98 [==============================] - 0s 3ms/sample - loss: 2.2224e-04 - mae: 0.0115 - mape: 100.4453 - val_loss: 1.4157e-04 - val_mae: 0.0100 - val_mape: 100.4932
Epoch 12/20
96/98 [============================>.] - ETA: 0s - loss: 2.3725e-04 - mae: 0.0120 - mape: 111.5529
Epoch 00012: val_loss did not improve from 0.00012
98/98 [==============================] - 0s 3ms/sample - loss: 2.3321e-04 - mae: 0.0119 - mape: 111.3951 - val_loss: 1.4736e-04 - val_mae: 0.0102 - val_mape: 112.9158
Epoch 13/20
96

Epoch 15/20
96/99 [============================>.] - ETA: 0s - loss: 2.2289e-04 - mae: 0.0115 - mape: 112.1484
Epoch 00015: val_loss did not improve from 0.00012
99/99 [==============================] - 0s 3ms/sample - loss: 2.2074e-04 - mae: 0.0115 - mape: 112.3960 - val_loss: 1.5387e-04 - val_mae: 0.0100 - val_mape: 93.8692
Epoch 16/20
96/99 [============================>.] - ETA: 0s - loss: 2.2414e-04 - mae: 0.0115 - mape: 103.3769
Epoch 00016: val_loss did not improve from 0.00012
99/99 [==============================] - 0s 3ms/sample - loss: 2.2256e-04 - mae: 0.0115 - mape: 102.3811 - val_loss: 1.5568e-04 - val_mae: 0.0101 - val_mape: 91.1483
Epoch 17/20
96/99 [============================>.] - ETA: 0s - loss: 2.2690e-04 - mae: 0.0117 - mape: 102.8078
Epoch 00017: val_loss did not improve from 0.00012
99/99 [==============================] - 0s 3ms/sample - loss: 2.2212e-04 - mae: 0.0115 - mape: 102.2221 - val_loss: 1.5414e-04 - val_mae: 0.0100 - val_mape: 93.4130
Epoch 18/20
96/9

Epoch 20/20
 96/100 [===========================>..] - ETA: 0s - loss: 2.2903e-04 - mae: 0.0117 - mape: 136.6854
Epoch 00020: val_loss did not improve from 0.00012
100/100 [==============================] - 0s 3ms/sample - loss: 2.2157e-04 - mae: 0.0115 - mape: 134.2632 - val_loss: 1.5650e-04 - val_mae: 0.0100 - val_mape: 115.7724
Train on 101 samples, validate on 60 samples
Epoch 1/20
 96/101 [===========================>..] - ETA: 0s - loss: 2.2168e-04 - mae: 0.0114 - mape: 134.3321
Epoch 00001: val_loss did not improve from 0.00012
101/101 [==============================] - 0s 3ms/sample - loss: 2.1739e-04 - mae: 0.0114 - mape: 133.4066 - val_loss: 1.5548e-04 - val_mae: 0.0100 - val_mape: 110.6007
Epoch 2/20
 96/101 [===========================>..] - ETA: 0s - loss: 2.2285e-04 - mae: 0.0115 - mape: 125.9324
Epoch 00002: val_loss did not improve from 0.00012
101/101 [==============================] - 0s 3ms/sample - loss: 2.1605e-04 - mae: 0.0113 - mape: 124.2981 - val_loss: 1.5507e-

...

Epoch 3/20
384/413 [==========================>...] - ETA: 0s - loss: 1.2944e-04 - mae: 0.0083 - mape: 144.2899
Epoch 00003: val_loss did not improve from 0.00002
413/413 [==============================] - 1s 3ms/sample - loss: 1.2754e-04 - mae: 0.0083 - mape: 142.8486 - val_loss: 3.9109e-05 - val_mae: 0.0042 - val_mape: 142.7230
Epoch 4/20
384/413 [==========================>...] - ETA: 0s - loss: 1.3497e-04 - mae: 0.0086 - mape: 127.8196
Epoch 00004: val_loss did not improve from 0.00002
413/413 [==============================] - 1s 3ms/sample - loss: 1.2864e-04 - mae: 0.0083 - mape: 126.0996 - val_loss: 4.0974e-05 - val_mae: 0.0044 - val_mape: 182.8989
Epoch 5/20
384/413 [==========================>...] - ETA: 0s - loss: 1.2303e-04 - mae: 0.0082 - mape: 159.4524
Epoch 00005: val_loss did not improve from 0.00002
413/413 [==============================] - 1s 3ms/sample - loss: 1.2792e-04 - mae: 0.0083 - mape: 160.3736 - val_loss: 3.9843e-05 - val_mae: 0.0042 - val_mape: 161.0687
Epoc

Epoch 8/20
384/414 [==========================>...] - ETA: 0s - loss: 1.3051e-04 - mae: 0.0084 - mape: 140.1278
Epoch 00008: val_loss did not improve from 0.00002
414/414 [==============================] - 1s 3ms/sample - loss: 1.2871e-04 - mae: 0.0083 - mape: 139.8127 - val_loss: 3.9202e-05 - val_mae: 0.0042 - val_mape: 140.3978
Epoch 9/20
384/414 [==========================>...] - ETA: 0s - loss: 1.2731e-04 - mae: 0.0084 - mape: 161.3033
Epoch 00009: val_loss did not improve from 0.00002
414/414 [==============================] - 1s 3ms/sample - loss: 1.2999e-04 - mae: 0.0083 - mape: 164.7697 - val_loss: 4.0048e-05 - val_mae: 0.0043 - val_mape: 168.2613
Epoch 10/20
384/414 [==========================>...] - ETA: 0s - loss: 1.2856e-04 - mae: 0.0083 - mape: 116.4132
Epoch 00010: val_loss did not improve from 0.00002
414/414 [==============================] - 1s 3ms/sample - loss: 1.3064e-04 - mae: 0.0085 - mape: 115.0204 - val_loss: 3.9055e-05 - val_mae: 0.0042 - val_mape: 126.6549
Epo

Epoch 13/20
384/415 [==========================>...] - ETA: 0s - loss: 1.2665e-04 - mae: 0.0082 - mape: 125.5718
Epoch 00013: val_loss did not improve from 0.00002
415/415 [==============================] - 1s 3ms/sample - loss: 1.2780e-04 - mae: 0.0083 - mape: 128.9435 - val_loss: 3.9807e-05 - val_mae: 0.0043 - val_mape: 148.8149
Epoch 14/20
384/415 [==========================>...] - ETA: 0s - loss: 1.3179e-04 - mae: 0.0084 - mape: 165.0735
Epoch 00014: val_loss did not improve from 0.00002
415/415 [==============================] - 1s 3ms/sample - loss: 1.2818e-04 - mae: 0.0083 - mape: 165.5516 - val_loss: 4.0745e-05 - val_mae: 0.0044 - val_mape: 176.8052
Epoch 15/20
384/415 [==========================>...] - ETA: 0s - loss: 1.2392e-04 - mae: 0.0082 - mape: 148.0376
Epoch 00015: val_loss did not improve from 0.00002
415/415 [==============================] - 1s 3ms/sample - loss: 1.2743e-04 - mae: 0.0083 - mape: 150.5341 - val_loss: 3.9708e-05 - val_mae: 0.0043 - val_mape: 144.0375
E

Epoch 18/20
384/416 [==========================>...] - ETA: 0s - loss: 1.2701e-04 - mae: 0.0083 - mape: 141.0959
Epoch 00018: val_loss did not improve from 0.00002
416/416 [==============================] - 1s 3ms/sample - loss: 1.2713e-04 - mae: 0.0083 - mape: 143.0203 - val_loss: 4.0011e-05 - val_mae: 0.0043 - val_mape: 159.0925
Epoch 19/20
384/416 [==========================>...] - ETA: 0s - loss: 1.1992e-04 - mae: 0.0082 - mape: 151.6732
Epoch 00019: val_loss did not improve from 0.00002
416/416 [==============================] - 1s 3ms/sample - loss: 1.2718e-04 - mae: 0.0083 - mape: 147.5506 - val_loss: 3.9522e-05 - val_mae: 0.0043 - val_mape: 119.3646
Epoch 20/20
384/416 [==========================>...] - ETA: 0s - loss: 1.2787e-04 - mae: 0.0083 - mape: 129.8854
Epoch 00020: val_loss did not improve from 0.00002
416/416 [==============================] - 1s 3ms/sample - loss: 1.2803e-04 - mae: 0.0083 - mape: 145.3912 - val_loss: 3.9608e-05 - val_mae: 0.0042 - val_mape: 144.1281
T

Epoch 7/20
416/419 [============================>.] - ETA: 0s - loss: 1.2673e-04 - mae: 0.0082 - mape: 153.0377
Epoch 00007: val_loss did not improve from 0.00002
419/419 [==============================] - 1s 3ms/sample - loss: 1.2638e-04 - mae: 0.0082 - mape: 152.4040 - val_loss: 3.9911e-05 - val_mae: 0.0043 - val_mape: 145.9394
Epoch 8/20
416/419 [============================>.] - ETA: 0s - loss: 1.2733e-04 - mae: 0.0083 - mape: 126.9723
Epoch 00008: val_loss did not improve from 0.00002
419/419 [==============================] - 1s 3ms/sample - loss: 1.2650e-04 - mae: 0.0083 - mape: 126.5616 - val_loss: 3.9735e-05 - val_mae: 0.0043 - val_mape: 125.6679
Epoch 9/20
416/419 [============================>.] - ETA: 0s - loss: 1.2683e-04 - mae: 0.0083 - mape: 132.4506
Epoch 00009: val_loss did not improve from 0.00002
419/419 [==============================] - 1s 3ms/sample - loss: 1.2603e-04 - mae: 0.0082 - mape: 132.9908 - val_loss: 4.0232e-05 - val_mae: 0.0043 - val_mape: 157.9818
Epoc

In [32]:
r2_oos_mean(data.loc[oos_start_idx:,bond_group].reset_index(drop = True),
            transformer_pred,data.loc[oos_start_idx:,'mean_' + str(bond_group)].reset_index(drop = True))

0.008985254082053862

# seq_len=12

In [17]:
holdout_start_idx

156

In [24]:
oos_end_idx-11+1

469

In [45]:
valid = 5*12

In [25]:
y_preds = []

for t in range(holdout_start_idx,oos_end_idx-11+1):
    x_train = data[factors][:t-valid]
    x_train = np.array(x_train)
    y_train = data["ALL"][:t-valid]
    y_train = np.array(y_train)

    Xtrain, ytrain = [], []
    for i in range(seq_len, len(x_train)):
        Xtrain.append(x_train[i-seq_len:i]) 
        ytrain.append(y_train[i])
    Xtrain, ytrain = np.array(Xtrain), np.array(ytrain)

    x_valid = data[factors][t-valid:t]
    x_valid = np.array(x_valid)
    y_valid = data["ALL"][t-valid:t]
    y_valid = np.array(y_valid)

    Xval, yval = [], []
    for i in range(seq_len, len(x_valid)):
        Xval.append(x_valid[i-seq_len:i])
        yval.append(y_valid[i])
    Xval, yval = np.array(Xval), np.array(yval)

    x_pred = data[factors][t:t+12]
    x_pred = np.array(x_pred)
    y_pred = data["ALL"][t:t+12]
    y_pred = np.array(y_pred)

    Xtest, ytest = [], []
    Xtest.append(x_pred[0:12])
    ytest.append(y_pred[11])    
    Xtest, ytest = np.array(Xtest), np.array(ytest)

    model.fit(Xtrain, ytrain, 
                batch_size=batch_size, 
                epochs=10, 
                callbacks=[callback],
                validation_data=(Xval, yval))  

    y_pred = model.predict(Xtest).squeeze().tolist()
    y_preds.append(y_pred)

Train on 84 samples, validate on 48 samples
Epoch 1/10
64/84 [=====================>........] - ETA: 25s - loss: 2.2070e-04 - mae: 0.0114 - mape: 208.1949
Epoch 00001: val_loss improved from inf to 0.00012, saving model to Transformer+TimeEmbedding.hdf5
84/84 [==============================] - 87s 1s/sample - loss: 2.0541e-04 - mae: 0.0108 - mape: 191.8753 - val_loss: 1.1975e-04 - val_mae: 0.0089 - val_mape: 97.8577
Epoch 2/10
64/84 [=====================>........] - ETA: 0s - loss: 1.8324e-04 - mae: 0.0109 - mape: 112.6764
Epoch 00002: val_loss improved from 0.00012 to 0.00012, saving model to Transformer+TimeEmbedding.hdf5
84/84 [==============================] - 1s 10ms/sample - loss: 1.7189e-04 - mae: 0.0104 - mape: 107.3216 - val_loss: 1.1900e-04 - val_mae: 0.0088 - val_mape: 100.9758
Epoch 3/10
64/84 [=====================>........] - ETA: 0s - loss: 1.7532e-04 - mae: 0.0104 - mape: 129.0865
Epoch 00003: val_loss improved from 0.00012 to 0.00012, saving model to Transformer+TimeE

Epoch 9/10
64/88 [====================>.........] - ETA: 0s - loss: 1.7734e-04 - mae: 0.0101 - mape: 97.9690
Epoch 00009: val_loss did not improve from 0.00011
88/88 [==============================] - 0s 4ms/sample - loss: 1.6127e-04 - mae: 0.0100 - mape: 97.7368 - val_loss: 1.6297e-04 - val_mae: 0.0102 - val_mape: 91.6371
Epoch 10/10
64/88 [====================>.........] - ETA: 0s - loss: 1.3350e-04 - mae: 0.0093 - mape: 111.7825
Epoch 00010: val_loss did not improve from 0.00011
88/88 [==============================] - 0s 4ms/sample - loss: 1.5795e-04 - mae: 0.0100 - mape: 126.1411 - val_loss: 1.5720e-04 - val_mae: 0.0097 - val_mape: 93.6246
Train on 89 samples, validate on 48 samples
Epoch 1/10
64/89 [====================>.........] - ETA: 0s - loss: 1.8615e-04 - mae: 0.0108 - mape: 133.0073
Epoch 00001: val_loss did not improve from 0.00011
89/89 [==============================] - 0s 4ms/sample - loss: 1.6219e-04 - mae: 0.0099 - mape: 134.4594 - val_loss: 1.5580e-04 - val_mae: 0.0

Epoch 4/10
64/91 [====================>.........] - ETA: 0s - loss: 1.4010e-04 - mae: 0.0092 - mape: 209.4529
Epoch 00004: val_loss did not improve from 0.00011
91/91 [==============================] - 0s 4ms/sample - loss: 1.7269e-04 - mae: 0.0103 - mape: 175.0228 - val_loss: 1.5962e-04 - val_mae: 0.0098 - val_mape: 113.3985
Epoch 5/10
64/91 [====================>.........] - ETA: 0s - loss: 1.6834e-04 - mae: 0.0101 - mape: 152.8125
Epoch 00005: val_loss did not improve from 0.00011
91/91 [==============================] - 0s 4ms/sample - loss: 1.6200e-04 - mae: 0.0101 - mape: 135.0267 - val_loss: 1.5911e-04 - val_mae: 0.0100 - val_mape: 91.1221
Epoch 6/10
64/91 [====================>.........] - ETA: 0s - loss: 1.7668e-04 - mae: 0.0105 - mape: 113.9046
Epoch 00006: val_loss did not improve from 0.00011
91/91 [==============================] - 0s 4ms/sample - loss: 1.6775e-04 - mae: 0.0104 - mape: 110.1622 - val_loss: 1.6018e-04 - val_mae: 0.0101 - val_mape: 89.4556
Epoch 7/10
64/91 [

Epoch 9/10
64/93 [===================>..........] - ETA: 0s - loss: 1.5270e-04 - mae: 0.0102 - mape: 103.5222
Epoch 00009: val_loss did not improve from 0.00011
93/93 [==============================] - 0s 4ms/sample - loss: 1.5847e-04 - mae: 0.0100 - mape: 108.2806 - val_loss: 1.6414e-04 - val_mae: 0.0102 - val_mape: 94.9194
Epoch 10/10
64/93 [===================>..........] - ETA: 0s - loss: 1.5160e-04 - mae: 0.0096 - mape: 106.4490
Epoch 00010: val_loss did not improve from 0.00011
93/93 [==============================] - 0s 4ms/sample - loss: 1.5531e-04 - mae: 0.0097 - mape: 107.3292 - val_loss: 1.6204e-04 - val_mae: 0.0101 - val_mape: 92.0928
Train on 94 samples, validate on 48 samples
Epoch 1/10
64/94 [===================>..........] - ETA: 0s - loss: 1.8182e-04 - mae: 0.0106 - mape: 115.3064
Epoch 00001: val_loss did not improve from 0.00011
94/94 [==============================] - 0s 4ms/sample - loss: 1.5770e-04 - mae: 0.0098 - mape: 115.6457 - val_loss: 1.6752e-04 - val_mae: 0

Epoch 4/10
64/96 [===================>..........] - ETA: 0s - loss: 1.3860e-04 - mae: 0.0091 - mape: 117.3101
Epoch 00004: val_loss did not improve from 0.00011
96/96 [==============================] - 0s 4ms/sample - loss: 1.5369e-04 - mae: 0.0098 - mape: 125.6021 - val_loss: 1.6707e-04 - val_mae: 0.0105 - val_mape: 106.4544
Epoch 5/10
64/96 [===================>..........] - ETA: 0s - loss: 1.6703e-04 - mae: 0.0102 - mape: 121.0539
Epoch 00005: val_loss did not improve from 0.00011
96/96 [==============================] - 0s 5ms/sample - loss: 1.5068e-04 - mae: 0.0097 - mape: 128.4444 - val_loss: 1.7123e-04 - val_mae: 0.0107 - val_mape: 114.5883
Epoch 6/10
64/96 [===================>..........] - ETA: 0s - loss: 1.5316e-04 - mae: 0.0096 - mape: 115.3554
Epoch 00006: val_loss did not improve from 0.00011
96/96 [==============================] - 0s 4ms/sample - loss: 1.4879e-04 - mae: 0.0097 - mape: 110.2358 - val_loss: 1.6589e-04 - val_mae: 0.0104 - val_mape: 111.9719
Epoch 7/10
64/96

...

Epoch 00006: val_loss did not improve from 0.00002
376/376 [==============================] - 2s 4ms/sample - loss: 1.1920e-04 - mae: 0.0082 - mape: 127.2270 - val_loss: 1.9970e-05 - val_mae: 0.0035 - val_mape: 157.9337
Epoch 7/10
352/376 [===========================>..] - ETA: 0s - loss: 1.1880e-04 - mae: 0.0081 - mape: 151.8706
Epoch 00007: val_loss did not improve from 0.00002
376/376 [==============================] - 2s 4ms/sample - loss: 1.1833e-04 - mae: 0.0081 - mape: 160.7911 - val_loss: 2.4824e-05 - val_mae: 0.0039 - val_mape: 216.6042
Epoch 8/10
352/376 [===========================>..] - ETA: 0s - loss: 1.2237e-04 - mae: 0.0083 - mape: 144.5419
Epoch 00008: val_loss did not improve from 0.00002
376/376 [==============================] - 2s 4ms/sample - loss: 1.1882e-04 - mae: 0.0082 - mape: 151.4266 - val_loss: 2.1429e-05 - val_mae: 0.0036 - val_mape: 178.0692
Epoch 9/10
352/376 [===========================>..] - ETA: 0s - loss: 1.1344e-04 - mae: 0.0080 - mape: 156.0039
Epoc

Train on 379 samples, validate on 48 samples
Epoch 1/10
352/379 [==========================>...] - ETA: 0s - loss: 1.2095e-04 - mae: 0.0083 - mape: 169.0673
Epoch 00001: val_loss did not improve from 0.00002
379/379 [==============================] - 2s 5ms/sample - loss: 1.2023e-04 - mae: 0.0082 - mape: 172.6306 - val_loss: 2.3849e-05 - val_mae: 0.0038 - val_mape: 189.6950
Epoch 2/10
352/379 [==========================>...] - ETA: 0s - loss: 1.1790e-04 - mae: 0.0081 - mape: 137.6749
Epoch 00002: val_loss did not improve from 0.00002
379/379 [==============================] - 2s 4ms/sample - loss: 1.1898e-04 - mae: 0.0082 - mape: 136.3598 - val_loss: 1.8870e-05 - val_mae: 0.0033 - val_mape: 131.0769
Epoch 3/10
352/379 [==========================>...] - ETA: 0s - loss: 1.2268e-04 - mae: 0.0083 - mape: 129.3174
Epoch 00003: val_loss did not improve from 0.00002
379/379 [==============================] - 2s 4ms/sample - loss: 1.1880e-04 - mae: 0.0082 - mape: 134.4141 - val_loss: 2.4180e-0

Epoch 10/10
352/383 [==========================>...] - ETA: 0s - loss: 1.1029e-04 - mae: 0.0080 - mape: 137.2731
Epoch 00010: val_loss did not improve from 0.00002
383/383 [==============================] - 2s 4ms/sample - loss: 1.1811e-04 - mae: 0.0082 - mape: 135.7814 - val_loss: 2.3095e-05 - val_mae: 0.0038 - val_mape: 178.8208
Train on 384 samples, validate on 48 samples
Epoch 1/10
352/384 [==========================>...] - ETA: 0s - loss: 1.1312e-04 - mae: 0.0080 - mape: 157.8890
Epoch 00001: val_loss did not improve from 0.00002
384/384 [==============================] - 2s 4ms/sample - loss: 1.1791e-04 - mae: 0.0081 - mape: 155.4715 - val_loss: 2.2237e-05 - val_mae: 0.0037 - val_mape: 173.0702
Epoch 2/10
352/384 [==========================>...] - ETA: 0s - loss: 1.1622e-04 - mae: 0.0081 - mape: 169.2538
Epoch 00002: val_loss did not improve from 0.00002
384/384 [==============================] - 2s 4ms/sample - loss: 1.1878e-04 - mae: 0.0082 - mape: 164.4857 - val_loss: 1.9311e-

Epoch 9/10
384/388 [============================>.] - ETA: 0s - loss: 1.1763e-04 - mae: 0.0081 - mape: 141.5331
Epoch 00009: val_loss did not improve from 0.00002
388/388 [==============================] - 2s 5ms/sample - loss: 1.1651e-04 - mae: 0.0081 - mape: 142.0562 - val_loss: 2.2869e-05 - val_mae: 0.0036 - val_mape: 153.4499
Epoch 10/10
384/388 [============================>.] - ETA: 0s - loss: 1.1440e-04 - mae: 0.0080 - mape: 149.2902
Epoch 00010: val_loss did not improve from 0.00002
388/388 [==============================] - 2s 5ms/sample - loss: 1.1650e-04 - mae: 0.0081 - mape: 149.0197 - val_loss: 2.1221e-05 - val_mae: 0.0035 - val_mape: 134.4665
Train on 389 samples, validate on 48 samples
Epoch 1/10
384/389 [============================>.] - ETA: 0s - loss: 1.1852e-04 - mae: 0.0082 - mape: 109.2639
Epoch 00001: val_loss did not improve from 0.00002
389/389 [==============================] - 2s 5ms/sample - loss: 1.1821e-04 - mae: 0.0082 - mape: 109.3307 - val_loss: 2.0948e-

Epoch 8/10
384/393 [============================>.] - ETA: 0s - loss: 1.1583e-04 - mae: 0.0080 - mape: 161.1230
Epoch 00008: val_loss did not improve from 0.00002
393/393 [==============================] - 2s 5ms/sample - loss: 1.1546e-04 - mae: 0.0080 - mape: 160.1305 - val_loss: 2.2899e-05 - val_mae: 0.0037 - val_mape: 144.6635
Epoch 9/10
384/393 [============================>.] - ETA: 0s - loss: 1.1633e-04 - mae: 0.0081 - mape: 133.4343
Epoch 00009: val_loss did not improve from 0.00002
393/393 [==============================] - 2s 5ms/sample - loss: 1.1539e-04 - mae: 0.0080 - mape: 136.7064 - val_loss: 2.2941e-05 - val_mae: 0.0037 - val_mape: 145.2826
Epoch 10/10
384/393 [============================>.] - ETA: 0s - loss: 1.1466e-04 - mae: 0.0080 - mape: 157.1751
Epoch 00010: val_loss did not improve from 0.00002
393/393 [==============================] - 2s 5ms/sample - loss: 1.1583e-04 - mae: 0.0080 - mape: 155.3925 - val_loss: 2.3694e-05 - val_mae: 0.0037 - val_mape: 155.8822
Tra

In [63]:
y_pred

0.003112510545179248

In [27]:
y_preds = pd.Series(y_preds)

In [50]:
y_preds

0      0.003259
1      0.003459
2      0.001828
3      0.002939
4      0.002019
         ...   
308    0.002857
309    0.002493
310    0.002227
311    0.002181
312    0.001994
Length: 313, dtype: float64

In [73]:
y_true = data["ALL"][holdout_start_idx+11:469+11].reset_index(drop = True)

In [74]:
y_true

0     -0.000480
1      0.013337
2      0.021967
3      0.001660
4      0.010620
         ...   
308    0.002278
309   -0.001622
310    0.001310
311    0.005592
312    0.002901
Name: ALL, Length: 313, dtype: float64

In [75]:
y_mean = data['mean_ALL'][holdout_start_idx+11:469+11].reset_index(drop = True)

In [76]:
y_mean

0      0.002123
1      0.002108
2      0.002174
3      0.002290
4      0.002286
         ...   
308    0.001971
309    0.001972
310    0.001964
311    0.001963
312    0.001971
Name: mean_ALL, Length: 313, dtype: float64

In [77]:
r2_oos(y_true, y_preds)

0.003706515880215089

In [78]:
r2_oos_mean(y_true, y_preds, y_mean)

-0.04099021887214516

In [60]:
y_preds = []

for t in range(holdout_start_idx,holdout_start_idx+120):
    x_train = data[factors][:t-valid]
    x_train = np.array(x_train)
    y_train = data["ALL"][:t-valid]
    y_train = np.array(y_train)

    Xtrain, ytrain = [], []
    for i in range(seq_len, len(x_train)):
        Xtrain.append(x_train[i-seq_len:i]) 
        ytrain.append(y_train[i])
    Xtrain, ytrain = np.array(Xtrain), np.array(ytrain)

    x_valid = data[factors][t-valid:t]
    x_valid = np.array(x_valid)
    y_valid = data["ALL"][t-valid:t]
    y_valid = np.array(y_valid)

    Xval, yval = [], []
    for i in range(seq_len, len(x_valid)):
        Xval.append(x_valid[i-seq_len:i])
        yval.append(y_valid[i])
    Xval, yval = np.array(Xval), np.array(yval)

    x_pred = data[factors][t:t+12]
    x_pred = np.array(x_pred)
    y_pred = data["ALL"][t:t+12]
    y_pred = np.array(y_pred)

    Xtest, ytest = [], []
    Xtest.append(x_pred[0:12])
    ytest.append(y_pred[11])    
    Xtest, ytest = np.array(Xtest), np.array(ytest)

    model.fit(Xtrain, ytrain, 
                batch_size=batch_size, 
                epochs=10, 
                callbacks=[callback],
                validation_data=(Xval, yval))  

    y_pred = model.predict(Xtest).squeeze().tolist()
    y_preds.append(y_pred)

Train on 84 samples, validate on 48 samples
Epoch 1/10
64/84 [=====================>........] - ETA: 0s - loss: 1.9062e-04 - mae: 0.0108 - mape: 137.3548
Epoch 00001: val_loss did not improve from 0.00004
84/84 [==============================] - 0s 4ms/sample - loss: 1.6870e-04 - mae: 0.0103 - mape: 130.8122 - val_loss: 1.1754e-04 - val_mae: 0.0087 - val_mape: 112.9864
Epoch 2/10
64/84 [=====================>........] - ETA: 0s - loss: 1.5416e-04 - mae: 0.0097 - mape: 135.3852
Epoch 00002: val_loss did not improve from 0.00004
84/84 [==============================] - 0s 4ms/sample - loss: 1.6897e-04 - mae: 0.0103 - mape: 134.3953 - val_loss: 1.1744e-04 - val_mae: 0.0087 - val_mape: 116.5832
Epoch 3/10
64/84 [=====================>........] - ETA: 0s - loss: 1.5853e-04 - mae: 0.0100 - mape: 112.9297
Epoch 00003: val_loss did not improve from 0.00004
84/84 [==============================] - 0s 4ms/sample - loss: 1.6894e-04 - mae: 0.0103 - mape: 137.1342 - val_loss: 1.1745e-04 - val_mae: 

Epoch 6/10
64/86 [=====================>........] - ETA: 0s - loss: 1.9203e-04 - mae: 0.0109 - mape: 108.8165
Epoch 00006: val_loss did not improve from 0.00004
86/86 [==============================] - 0s 4ms/sample - loss: 1.6707e-04 - mae: 0.0103 - mape: 117.9553 - val_loss: 1.3063e-04 - val_mae: 0.0092 - val_mape: 100.7737
Epoch 7/10
64/86 [=====================>........] - ETA: 0s - loss: 1.6950e-04 - mae: 0.0107 - mape: 124.3655
Epoch 00007: val_loss did not improve from 0.00004
86/86 [==============================] - 0s 4ms/sample - loss: 1.6726e-04 - mae: 0.0103 - mape: 122.8011 - val_loss: 1.2979e-04 - val_mae: 0.0091 - val_mape: 105.5753
Epoch 8/10
64/86 [=====================>........] - ETA: 0s - loss: 1.4783e-04 - mae: 0.0096 - mape: 135.6378
Epoch 00008: val_loss did not improve from 0.00004
86/86 [==============================] - 0s 4ms/sample - loss: 1.6644e-04 - mae: 0.0102 - mape: 125.9913 - val_loss: 1.2949e-04 - val_mae: 0.0091 - val_mape: 107.9390
Epoch 9/10
64/86

Train on 89 samples, validate on 48 samples
Epoch 1/10
64/89 [====================>.........] - ETA: 0s - loss: 1.5093e-04 - mae: 0.0099 - mape: 133.6396
Epoch 00001: val_loss did not improve from 0.00004
89/89 [==============================] - 0s 4ms/sample - loss: 1.6346e-04 - mae: 0.0102 - mape: 123.6129 - val_loss: 1.5530e-04 - val_mae: 0.0096 - val_mape: 105.5322
Epoch 2/10
64/89 [====================>.........] - ETA: 0s - loss: 1.6884e-04 - mae: 0.0105 - mape: 127.2892
Epoch 00002: val_loss did not improve from 0.00004
89/89 [==============================] - 0s 4ms/sample - loss: 1.6320e-04 - mae: 0.0101 - mape: 125.4788 - val_loss: 1.5546e-04 - val_mae: 0.0096 - val_mape: 108.0869
Epoch 3/10
64/89 [====================>.........] - ETA: 0s - loss: 1.5203e-04 - mae: 0.0097 - mape: 128.1598
Epoch 00003: val_loss did not improve from 0.00004
89/89 [==============================] - 0s 4ms/sample - loss: 1.6311e-04 - mae: 0.0101 - mape: 129.0732 - val_loss: 1.5590e-04 - val_mae: 

Epoch 6/10
64/91 [====================>.........] - ETA: 0s - loss: 1.6219e-04 - mae: 0.0103 - mape: 140.4800
Epoch 00006: val_loss did not improve from 0.00004
91/91 [==============================] - 0s 4ms/sample - loss: 1.6355e-04 - mae: 0.0102 - mape: 132.1528 - val_loss: 1.5967e-04 - val_mae: 0.0098 - val_mape: 115.0921
Epoch 7/10
64/91 [====================>.........] - ETA: 0s - loss: 1.4601e-04 - mae: 0.0095 - mape: 130.2893
Epoch 00007: val_loss did not improve from 0.00004
91/91 [==============================] - 0s 4ms/sample - loss: 1.6321e-04 - mae: 0.0102 - mape: 130.9574 - val_loss: 1.5949e-04 - val_mae: 0.0098 - val_mape: 113.6706
Epoch 8/10
64/91 [====================>.........] - ETA: 0s - loss: 1.5789e-04 - mae: 0.0100 - mape: 127.8637
Epoch 00008: val_loss did not improve from 0.00004
91/91 [==============================] - 0s 4ms/sample - loss: 1.6334e-04 - mae: 0.0102 - mape: 130.4768 - val_loss: 1.5963e-04 - val_mae: 0.0098 - val_mape: 114.8272
Epoch 9/10
64/91

Train on 94 samples, validate on 48 samples
Epoch 1/10
64/94 [===================>..........] - ETA: 0s - loss: 1.4785e-04 - mae: 0.0098 - mape: 140.3876
Epoch 00001: val_loss did not improve from 0.00004
94/94 [==============================] - 0s 4ms/sample - loss: 1.6498e-04 - mae: 0.0103 - mape: 132.1429 - val_loss: 1.6313e-04 - val_mae: 0.0099 - val_mape: 117.2263
Epoch 2/10
64/94 [===================>..........] - ETA: 0s - loss: 1.8905e-04 - mae: 0.0111 - mape: 116.3390
Epoch 00002: val_loss did not improve from 0.00004
94/94 [==============================] - 0s 4ms/sample - loss: 1.6513e-04 - mae: 0.0103 - mape: 132.7340 - val_loss: 1.6322e-04 - val_mae: 0.0099 - val_mape: 117.8951
Epoch 3/10
64/94 [===================>..........] - ETA: 0s - loss: 1.8089e-04 - mae: 0.0107 - mape: 132.3523
Epoch 00003: val_loss did not improve from 0.00004
94/94 [==============================] - 0s 4ms/sample - loss: 1.6500e-04 - mae: 0.0103 - mape: 131.9871 - val_loss: 1.6310e-04 - val_mae: 

...

160/192 [========================>.....] - ETA: 0s - loss: 1.4679e-04 - mae: 0.0097 - mape: 130.4880
Epoch 00001: val_loss did not improve from 0.00004
192/192 [==============================] - 1s 4ms/sample - loss: 1.5474e-04 - mae: 0.0099 - mape: 126.4937 - val_loss: 4.7308e-05 - val_mae: 0.0056 - val_mape: 222.7528
Epoch 2/10
160/192 [========================>.....] - ETA: 0s - loss: 1.5880e-04 - mae: 0.0101 - mape: 121.7003
Epoch 00002: val_loss did not improve from 0.00004
192/192 [==============================] - 1s 4ms/sample - loss: 1.5460e-04 - mae: 0.0099 - mape: 121.4528 - val_loss: 4.7842e-05 - val_mae: 0.0056 - val_mape: 245.1222
Epoch 3/10
160/192 [========================>.....] - ETA: 0s - loss: 1.5328e-04 - mae: 0.0098 - mape: 139.6126
Epoch 00003: val_loss did not improve from 0.00004
192/192 [==============================] - 1s 4ms/sample - loss: 1.5441e-04 - mae: 0.0099 - mape: 133.0393 - val_loss: 4.9018e-05 - val_mae: 0.0056 - val_mape: 278.9480
Epoch 4/10
160/

Epoch 6/10
192/194 [============================>.] - ETA: 0s - loss: 1.5183e-04 - mae: 0.0099 - mape: 99.0204
Epoch 00006: val_loss did not improve from 0.00004
194/194 [==============================] - 1s 5ms/sample - loss: 1.5662e-04 - mae: 0.0100 - mape: 99.0397 - val_loss: 4.7676e-05 - val_mae: 0.0057 - val_mape: 135.8180
Epoch 7/10
192/194 [============================>.] - ETA: 0s - loss: 1.5572e-04 - mae: 0.0099 - mape: 122.9453
Epoch 00007: val_loss did not improve from 0.00004
194/194 [==============================] - 1s 5ms/sample - loss: 1.5525e-04 - mae: 0.0099 - mape: 125.5061 - val_loss: 5.2566e-05 - val_mae: 0.0057 - val_mape: 368.7260
Epoch 8/10
192/194 [============================>.] - ETA: 0s - loss: 1.5635e-04 - mae: 0.0098 - mape: 149.2347
Epoch 00008: val_loss did not improve from 0.00004
194/194 [==============================] - 1s 5ms/sample - loss: 1.5632e-04 - mae: 0.0098 - mape: 171.4961 - val_loss: 5.7318e-05 - val_mae: 0.0060 - val_mape: 432.8662
Epoch 

Train on 197 samples, validate on 48 samples
Epoch 1/10
192/197 [============================>.] - ETA: 0s - loss: 1.5309e-04 - mae: 0.0097 - mape: 146.4299
Epoch 00001: val_loss did not improve from 0.00004
197/197 [==============================] - 1s 5ms/sample - loss: 1.5182e-04 - mae: 0.0097 - mape: 144.8879 - val_loss: 4.8831e-05 - val_mae: 0.0056 - val_mape: 362.9969
Epoch 2/10
192/197 [============================>.] - ETA: 0s - loss: 1.5242e-04 - mae: 0.0097 - mape: 164.2013
Epoch 00002: val_loss did not improve from 0.00004
197/197 [==============================] - 1s 5ms/sample - loss: 1.5234e-04 - mae: 0.0097 - mape: 162.3407 - val_loss: 4.7173e-05 - val_mae: 0.0055 - val_mape: 312.1314
Epoch 3/10
192/197 [============================>.] - ETA: 0s - loss: 1.5268e-04 - mae: 0.0098 - mape: 127.9723
Epoch 00003: val_loss did not improve from 0.00004
197/197 [==============================] - 1s 5ms/sample - loss: 1.5155e-04 - mae: 0.0097 - mape: 126.6335 - val_loss: 4.6935e-0

192/199 [===========================>..] - ETA: 0s - loss: 1.4572e-04 - mae: 0.0095 - mape: 149.6468
Epoch 00005: val_loss did not improve from 0.00004
199/199 [==============================] - 1s 5ms/sample - loss: 1.4986e-04 - mae: 0.0096 - mape: 147.6629 - val_loss: 4.9096e-05 - val_mae: 0.0055 - val_mape: 257.5556
Epoch 6/10
192/199 [===========================>..] - ETA: 0s - loss: 1.5298e-04 - mae: 0.0097 - mape: 121.5300
Epoch 00006: val_loss did not improve from 0.00004
199/199 [==============================] - 1s 5ms/sample - loss: 1.5016e-04 - mae: 0.0097 - mape: 121.0172 - val_loss: 5.0329e-05 - val_mae: 0.0057 - val_mape: 181.4281
Epoch 7/10
192/199 [===========================>..] - ETA: 0s - loss: 1.5176e-04 - mae: 0.0097 - mape: 111.4506
Epoch 00007: val_loss did not improve from 0.00004
199/199 [==============================] - 1s 5ms/sample - loss: 1.5035e-04 - mae: 0.0097 - mape: 111.0889 - val_loss: 4.9247e-05 - val_mae: 0.0056 - val_mape: 225.7921
Epoch 8/10
192/

Epoch 10/10
192/201 [===========================>..] - ETA: 0s - loss: 1.4877e-04 - mae: 0.0096 - mape: 128.2367
Epoch 00010: val_loss did not improve from 0.00004
201/201 [==============================] - 1s 5ms/sample - loss: 1.4815e-04 - mae: 0.0096 - mape: 126.4494 - val_loss: 5.1685e-05 - val_mae: 0.0057 - val_mape: 209.0936
Train on 202 samples, validate on 48 samples
Epoch 1/10
192/202 [===========================>..] - ETA: 0s - loss: 1.4775e-04 - mae: 0.0096 - mape: 112.0386
Epoch 00001: val_loss did not improve from 0.00004
202/202 [==============================] - 1s 5ms/sample - loss: 1.4768e-04 - mae: 0.0096 - mape: 120.5886 - val_loss: 5.1086e-05 - val_mae: 0.0057 - val_mape: 230.1243
Epoch 2/10
192/202 [===========================>..] - ETA: 0s - loss: 1.5168e-04 - mae: 0.0097 - mape: 127.6842
Epoch 00002: val_loss did not improve from 0.00004
202/202 [==============================] - 1s 5ms/sample - loss: 1.4717e-04 - mae: 0.0095 - mape: 128.5370 - val_loss: 5.0773e-

In [63]:
y_preds = pd.Series(y_preds)

In [64]:
y_preds

0      0.003759
1      0.003480
2      0.003423
3      0.003189
4      0.002880
         ...   
115    0.002064
116    0.002212
117    0.001979
118    0.002684
119    0.003399
Length: 120, dtype: float64

In [71]:
y_true = data["ALL"][holdout_start_idx+12:holdout_start_idx+120+12].reset_index(drop = True)

In [69]:
y_mean = data['mean_ALL'][holdout_start_idx+12:holdout_start_idx+120+12].reset_index(drop = True)

In [73]:
r2_oos(y_true, y_preds)

0.06780181625459103

In [72]:
r2_oos_mean(y_true, y_preds, y_mean)

0.009725125031824766

# method3

In [116]:
batch_size = 32
seq_len = 60

d_k = 256
d_v = 256
n_heads = 12
ff_dim = 256

In [150]:
df = data.copy()

In [151]:
df

month       3AL      3ALM      3ASM       3AS       2AL      2ALM  \
0    1981-01 -0.003205  0.023927 -0.003941  0.006082 -0.004262 -0.007570   
1    1981-02 -0.013603  0.024718 -0.004110 -0.021906 -0.014891 -0.047339   
2    1981-03  0.004491  0.025509 -0.004280  0.020417  0.002901  0.019075   
3    1981-04 -0.037980  0.026301 -0.004449 -0.026618 -0.035419 -0.046644   
4    1981-05  0.008354  0.027092 -0.004618  0.000327  0.011004  0.029250   
..       ...       ...       ...       ...       ...       ...       ...   
475  2020-08 -0.010657  0.001280 -0.001028  0.000275  0.001118  0.000100   
476  2020-09 -0.010657  0.001280  0.001048  0.000005 -0.003581 -0.000347   
477  2020-10 -0.010657  0.001280 -0.000351  0.000355  0.001079 -0.000527   
478  2020-11 -0.010657  0.001280  0.000142 -0.000390  0.003699 -0.000381   
479  2020-12 -0.010657  0.001280  0.001793  0.000231  0.001200 -0.000597   

         2ASM       2AS       1AL  ...   mean_3A   mean_2A   mean_1A  \
0   -0.000069 -0.009637 -0.007662  ...  0.004508  0.005384  0.012889   
1   -0.022836 -0.009374 -0.016383  ...  0.001638 -0.000453  0.002100   
2    0.013657  0.017874  0.006098  ... -0.003989 -0.005221 -0.004234   
3   -0.034813 -0.023500 -0.042539  ... -0.001018 -0.001104 -0.000949   
4    0.014513 -0.000429  0.009009  ... -0.007921 -0.007499 -0.007955   
..        ...       ...       ...  ...       ...       ...       ...   
475  0.000588 -0.000008  0.004087  ...  0.001139  0.001536  0.001852   
476 -0.001211  0.000081 -0.002820  ...  0.001135  0.001535  0.001854   
477  0.000056 -0.001752  0.001429  ...  0.001135  0.001528  0.001846   
478  0.000993  0.000071  0.008153  ...  0.001132  0.001525  0.001845   
479  0.000488  0.000049  0.003763  ...  0.001130  0.001525  0.001853   

      mean_3B   mean_JK    mean_L   mean_LM   mean_SM    mean_S  mean_ALL  
0    0.008977 -0.052297 -0.000420  0.002000  0.001193  0.006889  0.001343  
1   -0.002045 -0.014361 -0.002333  0.000381  0.003338  0.000902 -0.000874  
2   -0.009164 -0.008604 -0.006383 -0.008880 -0.001366 -0.003615 -0.005231  
3   -0.005679 -0.003247 -0.003388 -0.002516  0.002788  0.001733 -0.001530  
4   -0.013049 -0.005998 -0.010086 -0.007960 -0.003767 -0.003604 -0.007899  
..        ...       ...       ...       ...       ...       ...       ...  
475  0.002197  0.003088  0.002332  0.002279  0.001643  0.001146  0.001971  
476  0.002198  0.003091  0.002335  0.002273  0.001642  0.001145  0.001972  
477  0.002190  0.003092  0.002324  0.002266  0.001637  0.001142  0.001964  
478  0.002192  0.003092  0.002323  0.002266  0.001634  0.001141  0.001963  
479  0.002206  0.003115  0.002337  0.002267  0.001634  0.001143  0.001971  

[480 rows x 113 columns]

In [152]:
df['month'] = pd.to_datetime(df['month'],format = '%Y-%m').dt.to_period('M')

In [153]:
df['year'] = df['month'].dt.year

In [154]:
df['year']

0      1981
1      1981
2      1981
3      1981
4      1981
       ... 
475    2020
476    2020
477    2020
478    2020
479    2020
Name: year, Length: 480, dtype: int64

In [155]:
df_train = df[(df['year'] <= 2012)]

In [156]:
df_train

month       3AL      3ALM      3ASM       3AS       2AL      2ALM  \
0    1981-01 -0.003205  0.023927 -0.003941  0.006082 -0.004262 -0.007570   
1    1981-02 -0.013603  0.024718 -0.004110 -0.021906 -0.014891 -0.047339   
2    1981-03  0.004491  0.025509 -0.004280  0.020417  0.002901  0.019075   
3    1981-04 -0.037980  0.026301 -0.004449 -0.026618 -0.035419 -0.046644   
4    1981-05  0.008354  0.027092 -0.004618  0.000327  0.011004  0.029250   
..       ...       ...       ...       ...       ...       ...       ...   
379  2012-08  0.004019  0.001280  0.003771  0.002228  0.014412 -0.002980   
380  2012-09  0.003929  0.001280  0.000372  0.000299  0.004247  0.015625   
381  2012-10  0.003839  0.001280  0.001712 -0.001990  0.013005 -0.000953   
382  2012-11  0.003749  0.001280  0.000314  0.000450  0.003601 -0.000816   
383  2012-12  0.003659  0.001280  0.000288 -0.001190  0.002143  0.000061   

         2ASM       2AS       1AL  ...   mean_2A   mean_1A   mean_3B  \
0   -0.000069 -0.009637 -0.007662  ...  0.005384  0.012889  0.008977   
1   -0.022836 -0.009374 -0.016383  ... -0.000453  0.002100 -0.002045   
2    0.013657  0.017874  0.006098  ... -0.005221 -0.004234 -0.009164   
3   -0.034813 -0.023500 -0.042539  ... -0.001104 -0.000949 -0.005679   
4    0.014513 -0.000429  0.009009  ... -0.007499 -0.007955 -0.013049   
..        ...       ...       ...  ...       ...       ...       ...   
379  0.003616  0.001335  0.006921  ...  0.001750  0.001989  0.002319   
380  0.003060  0.000749  0.009127  ...  0.001761  0.001998  0.002332   
381  0.003633  0.001126  0.006584  ...  0.001764  0.002008  0.002376   
382  0.001491  0.000964  0.007602  ...  0.001772  0.002016  0.002393   
383  0.000520  0.000703  0.000218  ...  0.001773  0.002023  0.002387   

      mean_JK    mean_L   mean_LM   mean_SM    mean_S  mean_ALL  year  
0   -0.052297 -0.000420  0.002000  0.001193  0.006889  0.001343  1981  
1   -0.014361 -0.002333  0.000381  0.003338  0.000902 -0.000874  1981  
2   -0.008604 -0.006383 -0.008880 -0.001366 -0.003615 -0.005231  1981  
3   -0.003247 -0.003388 -0.002516  0.002788  0.001733 -0.001530  1981  
4   -0.005998 -0.010086 -0.007960 -0.003767 -0.003604 -0.007899  1981  
..        ...       ...       ...       ...       ...       ...   ...  
379  0.003471  0.002429  0.002503  0.001886  0.001331  0.002150  2012  
380  0.003468  0.002443  0.002505  0.001894  0.001330  0.002159  2012  
381  0.003497  0.002473  0.002545  0.001905  0.001330  0.002178  2012  
382  0.003513  0.002491  0.002551  0.001910  0.001328  0.002188  2012  
383  0.003511  0.002498  0.002543  0.001910  0.001324  0.002191  2012  

[384 rows x 114 columns]

In [159]:
df_val = df[(df['year'] >= 1993) & (df['year'] < 2000)]

In [160]:
df_test = df[(df['year'] >= 2000)]

In [126]:
df_test

month       3AL      3ALM      3ASM       3AS       2AL      2ALM  \
228  2000-01  0.001409 -0.009283 -0.012836 -0.004335 -0.018507 -0.002207   
229  2000-02 -0.008333 -0.007130 -0.004066 -0.005262 -0.000126  0.002978   
230  2000-03  0.000614 -0.003183  0.004704 -0.002409  0.000842 -0.010847   
231  2000-04 -0.037951  0.006284  0.007543  0.003943  0.000968 -0.000010   
232  2000-05  0.009413 -0.005723 -0.030261 -0.007401 -0.013086 -0.013324   
..       ...       ...       ...       ...       ...       ...       ...   
475  2020-08 -0.010657  0.001280 -0.001028  0.000275  0.001118  0.000100   
476  2020-09 -0.010657  0.001280  0.001048  0.000005 -0.003581 -0.000347   
477  2020-10 -0.010657  0.001280 -0.000351  0.000355  0.001079 -0.000527   
478  2020-11 -0.010657  0.001280  0.000142 -0.000390  0.003699 -0.000381   
479  2020-12 -0.010657  0.001280  0.001793  0.000231  0.001200 -0.000597   

         2ASM       2AS       1AL  ...    lag_2A    lag_1A    lag_3B  \
228 -0.008733 -0.006664 -0.017196  ... -0.003090 -0.001641  0.000631   
229 -0.006830 -0.005397 -0.005127  ... -0.012393 -0.013255 -0.011567   
230 -0.000464  0.000908  0.000666  ... -0.001523 -0.004201 -0.005096   
231  0.001436 -0.001698  0.001151  ... -0.001154  0.000506  0.000583   
232 -0.008028 -0.007399 -0.012353  ...  0.000645 -0.000250 -0.004755   
..        ...       ...       ...  ...       ...       ...       ...   
475  0.000588 -0.000008  0.004087  ...  0.002463  0.005726  0.015109   
476 -0.001211  0.000081 -0.002820  ...  0.000613  0.002797  0.002562   
477  0.000056 -0.001752  0.001429  ... -0.001600 -0.001993 -0.001732   
478  0.000993  0.000071  0.008153  ...  0.000036  0.001143  0.003399   
479  0.000488  0.000049  0.003763  ...  0.001648  0.005675  0.008770   

       lag_JK     lag_L    lag_LM    lag_SM     lag_S   lag_ALL  year  
228  0.003160 -0.001180  0.000380 -0.001343 -0.001929 -0.001007  2000  
229 -0.010518 -0.015640 -0.012033 -0.008855 -0.005732 -0.012337  2000  
230 -0.004100 -0.003751 -0.004680 -0.004023 -0.003233 -0.003912  2000  
231  0.000094  0.001146 -0.002270  0.000308 -0.000206  0.000153  2000  
232 -0.005911 -0.000844 -0.001771 -0.002406 -0.001280 -0.001487  2000  
..        ...       ...       ...       ...       ...       ...   ...  
475  0.020118  0.010417  0.006187  0.002954  0.004476  0.006978  2020  
476  0.004495  0.003713 -0.000553  0.000987  0.000874  0.002278  2020  
477  0.003173 -0.002543 -0.001350 -0.000805 -0.000353 -0.001622  2020  
478  0.003311  0.001859  0.002488  0.000547  0.000730  0.001310  2020  
479  0.013930  0.009032  0.002559  0.001540  0.001767  0.005592  2020  

[252 rows x 84 columns]

In [127]:
df_train[factors+['ALL']]

logDP     logDY     logEP     logDE      svar       b/m      ntis  \
0   -3.092812 -3.127273 -2.214911 -0.877901  0.002951  0.891503  0.026816   
1   -3.039518 -3.086339 -2.173502 -0.866016  0.001597  0.907239  0.028695   
2   -3.046276 -3.033087 -2.192134 -0.854143  0.001531  0.881816  0.030009   
3   -3.075285 -3.039886 -2.233004 -0.842281  0.002076  0.924921  0.027939   
4   -3.045727 -3.069463 -2.199488 -0.846239  0.000832  0.930594  0.027352   
..        ...       ...       ...       ...       ...       ...       ...   
379 -3.870940 -3.858421 -2.758317 -1.112623  0.001553  0.351594 -0.020321   
380 -3.875890 -3.856319 -2.783315 -1.092575  0.000727  0.349387 -0.019783   
381 -3.885427 -3.861480 -2.812719 -1.072708  0.001045  0.340383 -0.017426   
382 -3.846946 -3.866934 -2.792693 -1.054253  0.000926  0.349237 -0.015715   
383 -3.831631 -3.828788 -2.795497 -1.036134  0.001903  0.351138 -0.012094   

        tbl     lty     ltr  ...      infl       dmf      lev1      lev2  \
0    0.1549  0.1199  0.0352  ...  0.008255  0.154151  0.375463  0.412344   
1    0.1502  0.1211 -0.0115  ...  0.009357  0.155467  0.378569  0.425260   
2    0.1479  0.1283 -0.0435  ...  0.008111  0.156757  0.376936  0.424365   
3    0.1336  0.1248  0.0384  ...  0.010345  0.158023  0.365706  0.418989   
4    0.1369  0.1332 -0.0518  ...  0.006826  0.157967  0.366546  0.424636   
..      ...     ...     ...  ...       ...       ...       ...       ...   
379  0.0010  0.0216  0.0247  ... -0.001466  0.206879  0.344524  0.529663   
380  0.0010  0.0223 -0.0068  ... -0.001630  0.209754  0.341141  0.525817   
381  0.0011  0.0235 -0.0146  ...  0.005565  0.212564  0.337031  0.519015   
382  0.0010  0.0238 -0.0014  ...  0.004462  0.214883  0.341725  0.521562   
383  0.0009  0.0228  0.0144  ... -0.000389  0.217168  0.342686  0.522087   

         mmmf   onoff        ps     sp500    amihud       ALL  
0   -0.014979  0.8180 -0.013527 -0.033874  0.480474 -0.003091  
1    0.164924  0.0880  0.003796 -0.045742  0.476741 -0.013946  
2    0.141575 -0.0220  0.000643  0.013277  0.486135  0.009574  
3    0.124017  0.2780  0.013316  0.036033  0.378713 -0.033375  
4    0.045665 -0.1220  0.010069 -0.023456  0.336175  0.009176  
..        ...     ...       ...       ...       ...       ...  
379  0.004960 -0.8479  0.099783  0.012598  0.116899  0.005681  
380  0.004936 -0.8384 -0.022280  0.019763  0.108088  0.009435  
381  0.004911 -0.9635  0.036210  0.024236  0.084351  0.006071  
382  0.018584 -0.9801 -0.042412 -0.019789  0.095410  0.003123  
383  0.018245 -0.9456 -0.059050  0.002847  0.099907  0.000864  

[384 rows x 23 columns]

In [128]:
train_data = df_train[factors+['ALL']].values
val_data = df_val[factors+['ALL']].values
test_data = df_test[factors+['ALL']].values

In [129]:
print('Training data shape: {}'.format(train_data.shape))
print('Validation data shape: {}'.format(val_data.shape))
print('Test data shape: {}'.format(test_data.shape))

Training data shape: (384, 23)
Validation data shape: (84, 23)
Test data shape: (252, 23)


In [130]:
# Training data
X_train, y_train = [], []
for i in range(seq_len, len(train_data)):
    X_train.append(df_train[factors].values[i-seq_len:i]) 
    y_train.append(df_train['ALL'].values[i]) 
X_train, y_train = np.array(X_train), np.array(y_train)

In [131]:
# Validation data
X_val, y_val = [], []
for i in range(seq_len, len(val_data)):
    X_val.append(df_val[factors].values[i-seq_len:i])
    y_val.append(df_val['ALL'].values[i])
X_val, y_val = np.array(X_val), np.array(y_val)

In [132]:
# Test data
X_test, y_test = [], []
for i in range(seq_len, len(test_data)):
    X_test.append(df_test[factors].values[i-seq_len:i])
    y_test.append(df_test['ALL'].values[i])    
X_test, y_test = np.array(X_test), np.array(y_test)

In [133]:
print('Training set shape', X_train.shape, y_train.shape)
print('Validation set shape', X_val.shape, y_val.shape)
print('Testing set shape' ,X_test.shape, y_test.shape)

Training set shape (324, 60, 22) (324,)
Validation set shape (24, 60, 22) (24,)
Testing set shape (192, 60, 22) (192,)


In [134]:
model.fit(X_train, y_train, 
                    batch_size=batch_size, 
                    epochs=20, 
                    callbacks=[callback],
                    validation_data=(X_val, y_val))

Train on 324 samples, validate on 24 samples
Epoch 1/20
320/324 [============================>.] - ETA: 0s - loss: 1.1916e-04 - mae: 0.0082 - mape: 153.5603
Epoch 00001: val_loss improved from inf to 0.00004, saving model to Transformer+TimeEmbedding.hdf5
324/324 [==============================] - 82s 255ms/sample - loss: 1.2202e-04 - mae: 0.0083 - mape: 152.7129 - val_loss: 4.3370e-05 - val_mae: 0.0049 - val_mape: 313.0197
Epoch 2/20
320/324 [============================>.] - ETA: 0s - loss: 1.1383e-04 - mae: 0.0080 - mape: 179.3178
Epoch 00002: val_loss improved from 0.00004 to 0.00003, saving model to Transformer+TimeEmbedding.hdf5
324/324 [==============================] - 6s 19ms/sample - loss: 1.1379e-04 - mae: 0.0080 - mape: 178.3952 - val_loss: 2.6565e-05 - val_mae: 0.0040 - val_mape: 98.1133
Epoch 3/20
320/324 [============================>.] - ETA: 0s - loss: 1.1282e-04 - mae: 0.0080 - mape: 141.9129
Epoch 00003: val_loss did not improve from 0.00003
324/324 [================

In [135]:
test_pred = model.predict(X_test)

In [136]:
pred = np.array(test_pred).flatten()

In [170]:
pred = pd.Series(pred)

In [171]:
pred

0      0.002216
1      0.002215
2      0.002213
3      0.002213
4      0.002214
         ...   
187    0.002214
188    0.002211
189    0.002209
190    0.002215
191    0.002215
Length: 192, dtype: float32

In [138]:
test_eval = model.evaluate(X_test, y_test, verbose=0)

In [139]:
test_eval

[7.430432136364591e-05, 0.005824041, 150.55476]

In [172]:
y_test = pd.Series(y_test)

In [173]:
y_test

0     -0.001777
1     -0.002213
2     -0.012870
3      0.003982
4      0.004802
         ...   
187    0.002278
188   -0.001622
189    0.001310
190    0.005592
191    0.002901
Length: 192, dtype: float64

In [58]:
def r2_oos(y_true, y_pred):
    return 1 - np.sum((y_true - y_pred)**2) / np.sum(y_true**2)

In [177]:
r2_oos(y_true = y_test, y_pred = pred)

0.03458752848006241

In [183]:
y_mean = df_test['mean_ALL'][seq_len:len(test_data)].reset_index(drop = True)

In [181]:
y_mean = pd.Series(y_mean)

In [184]:
y_mean

0      0.002150
1      0.002137
2      0.002122
3      0.002070
4      0.002077
         ...   
187    0.001971
188    0.001972
189    0.001964
190    0.001963
191    0.001971
Name: mean_ALL, Length: 192, dtype: float64

In [179]:
def r2_oos_mean(y_true, y_pred, y_mean_pred): #普通R方
    return 1 - np.sum((y_true - y_pred)**2) / np.sum((y_true-y_mean_pred)**2)

In [185]:
r2_oos_mean(y_test, pred, y_mean)

0.0010960591663996544